In [7]:
## Note: Must stop program manually or let run through complete time steps 
################################## import statements #################################
import matplotlib.pyplot as plt
import os
import pygame
import random
from collections import defaultdict
import numpy as np
from random import randint
######################################################################################



####################################### Initialize ###################################
pygame.init()
global planets_made
planets_made = 0
######################################################################################


####################################### Classes ######################################
# Class to hold state of planet
class planet_state:
    def __init__(self, x, y, vx, vy):
        self.x = x 
        self.y = y
        self.vx = vx
        self.vy = vy
    def print_values(self):
        print('Print Planet State: ')
        print('x =', self.x)
        print('y =', self.y)
        print('vx =', self.vx)
        print('vy =', self.vy)

# Class to hold state of derivative
class derivative_state:
    def __init__(self, vx, vy, ax, ay):
        self.vx = vx 
        self.vy = vy
        self.ax = ax
        self.ay = ay
    def print_values(self):
        print('Print Derivative Values: ')
        print('vx = ', self.vx)
        print('vy = ', self.vy)
        print('ax = ', self.ax)
        print('ay = ', self.ay)

# Class for planet
class Planet:
    def __init__(self, mass, x, y, vx, vy, rho = 0.00334):
        global planets_made
        self.index = planets_made
        planets_made += 1
        self.Mass = mass
        self.State = planet_state(x, y, vx, vy)
        self.color = (255, 255, 255)
        self.rho = rho
        self.radius = 1.0 
        self.set_radius_from_mass()
        self.merged = False

    def print_values(self):
        print('Mass = ', self.Mass)
        print('Density = ', self.rho)
        print('Radius = ', self.radius)
        self.State.print_values()

    def acceleration(self, G, solar_system, state):
        ax = 0.0
        ay = 0.0
        for planet in solar_system:
            if planet is self or planet.merged:
                continue
            dx = planet.State.x - state.x
            dy = planet.State.y - state.y
            rs = (dx*dx + dy*dy)
            r = (dx*dx + dy*dy) ** 0.5
            force = G * planet.Mass * self.Mass / rs if rs > 1e-10 else 0
            ax += force * (dx/r)
            ay += force * (dy/r)
        return ax, ay

    def RK1(self, G, solar_system, state):
        ax, ay = self.acceleration(G, solar_system, self.State)
        return derivative_state(state.vx, state.vy, ax, ay)

    def RK2(self, G, solar_system, state, derivativeState, dt):
        newState = planet_state(0.0, 0.0, 0.0, 0.0)
        newState.x = state.x + derivativeState.vx * dt
        newState.y = state.y + derivativeState.vy * dt
        newState.vx = state.vx + derivativeState.ax * dt
        newState.vy = state.vy + derivativeState.ay * dt
        ax, ay = self.acceleration(G, solar_system, newState)
        return derivative_state(newState.vx, newState.vy, ax, ay)

    def update_position(self, G, solar_system, dt):
        k1 = self.RK1(G, solar_system, self.State)
        k2 = self.RK2(G, solar_system, self.State, k1, dt*0.5)
        k3 = self.RK2(G, solar_system, self.State, k2, dt*0.5)
        k4 = self.RK2(G, solar_system, self.State, k3, dt)

        dxdt = (1.0/6.0) * (k1.vx + 2.0 * (k2.vx + k3.vx) + k4.vx)
        dydt = (1.0/6.0) * (k1.vy + 2.0 * (k2.vy + k3.vy) + k4.vy)
        dvxdt = (1.0/6.0) * (k1.ax + 2.0 * (k2.ax + k3.ax) + k4.ax)
        dvydt = (1.0/6.0) * (k1.ay + 2.0 * (k2.ay + k3.ay) + k4.ay)

        self.State.x += dxdt * dt
        self.State.y += dydt * dt
        self.State.vx += dvxdt * dt
        self.State.vy += dvydt * dt

    def set_radius_from_mass(self):
        self.radius = abs((3.0 * self.Mass/(self.rho*4.0*np.pi))**(0.3333))
######################################################################################



################################## Other Functions ###################################
def updatePositoins(G, solar_system, dt):
    for i in range(len(solar_system)):
        if i > 0:
            current_planet = solar_system[i]
            current_planet.update_position(G, solar_system, dt)

def distance(planet1, planet2):
    dist = ((planet1.State.x - planet2.State.x)**2.0 + (planet1.State.y - planet2.State.y)**2.0)**0.5
    return dist

def planets_touch(planet1, planet2):
    dx = planet1.State.x - planet2.State.x
    dy = planet1.State.y - planet2.State.y
    dsq = dx*dx + dy*dy
    dr = dsq**0.5
    return dr <= (planet1.radius + planet2.radius)

def Angle(radius, mass, speed):
    angle = radius * mass * speed
    if angle > 360:
        angle -= 360
    angle_rad = np.radians(angle)
    return angle_rad

def momentum(radius, mass, velocity):
    angle = Angle(radius, mass, velocity)
    x_velocity = velocity * mass * np.cos(angle)
    y_velocity = velocity * mass * np.sin(angle)
    return x_velocity, y_velocity

def gravity(e):
    G1 = 6.674*10**(-20)
    G2 = G1 * (1/e)**3.0
    G = G2*(10**24)
    return G
######################################################################################



############################ Initialize Pygame window ################################
WIDTH, HEIGHT = 800, 800
WIDTHD2, HEIGHTD2 = WIDTH/2.0, HEIGHT/2.0
######################################################################################



####################################### Main #########################################
def main():
    pygame.init()
    screen = pygame.display.set_mode((WIDTH, HEIGHT))
    
    keysPressed = defaultdict(bool)

    def ScanKeyboard():
        while True:
            evt = pygame.event.poll()
            if evt.type == pygame.NOEVENT:
                break
            elif evt.type in [pygame.KEYDOWN, pygame.KEYUP]:
                keysPressed[evt.key] = evt.type == pygame.KEYDOWN

    G = gravity(10**2)
    solar_system = []
    earth_mass = 5.97
    moon_mass = 0.07342
    moon_velocity = 0.001022

    fragment_moon = True 
    
    # randomly adjusting things
    min_adjust_x, min_adjust_y = -2000.0, -2000.0
    max_adjust_x, max_adjust_y = 2000.0, 2000.0
    min_adjust_v = 1000.0
    max_adjust_v = 2000.0
    
    # moon starting positions
    moon_radius_x = 400.0 
    moon_radius_y = 400.0 - 189.946 

    limit = 1/300 # smallest final fragment
    split_int_min = 8
    split_int_max = 80

    Earth = Planet(earth_mass, 400.0, 400.0, 0.0, 0.0)
    solar_system.append(Earth)
    x_velocity, y_velocity = momentum(378.0, moon_mass, moon_velocity)
    moon1 = Planet(moon_mass, moon_radius_x, moon_radius_y, 25.0*x_velocity, 25.0*y_velocity )
    solar_system.append(moon1)
    
    i = 1 # number of things orbiting Earth

    if (fragment_moon == True):
        while (solar_system[i].Mass > limit * moon_mass):
            planet_to_split = solar_system[i]
            split_fraction = 1.0/(randint(split_int_min, split_int_max))
            massSplit = planet_to_split.Mass * split_fraction
            balance_momentum_mass = planet_to_split.Mass - massSplit
            solar_system[i].Mass = massSplit
            oldRadius = solar_system[i].radius
            solar_system[i].set_radius_from_mass()
            w = (randint(min_adjust_v, max_adjust_v))*10**(-5.0)
            solar_system[i].State.vx = moon_velocity*w
            solar_system[i].State.vy = moon_velocity*w
            Xvelo = ((planet_to_split.Mass * planet_to_split.State.vx) - (solar_system[i].Mass * solar_system[i].State.vx)) / balance_momentum_mass
            Yvelo = ((planet_to_split.Mass * planet_to_split.State.vy) - (solar_system[i].Mass * solar_system[i].State.vy)) / balance_momentum_mass
            adjustx = (randint(min_adjust_x, max_adjust_x))/1000.0
            adjusty = (randint(min_adjust_y, max_adjust_y))/1000.0
            moon2 = Planet(balance_momentum_mass, solar_system[i].State.x + oldRadius*adjustx, solar_system[i].State.y + oldRadius*adjusty, Xvelo, Yvelo )
            solar_system.append(moon2)
            i = i+1
  
    t = 0
    dt = 800

    bClearScreen = True
    zoom = 1.0
    pygame.display.set_caption('SPACE: showorbits, keypad +/-: zoom in/out')

    while t < 10**10:
        t += dt
        pygame.display.flip()
        
        if bClearScreen: # show orbits or not
            screen.fill((0,0,0))
        screen.lock()
        for i in range(len(solar_system)):
            pygame.draw.circle(screen, ((225-i)%225, 255, (255-i)%255), 
                              (int(WIDTHD2+zoom*WIDTHD2*(solar_system[i].State.x-WIDTHD2)/WIDTHD2), 
                              int(HEIGHTD2+zoom*HEIGHTD2*(solar_system[i].State.y-HEIGHTD2)/HEIGHTD2)),
                              int(solar_system[i].radius*zoom), 0)
            pygame.draw.circle(screen, (165,190,231), 
                              (int(WIDTHD2+zoom*WIDTHD2*(solar_system[i].State.x-WIDTHD2)/WIDTHD2),
                              int(HEIGHTD2+zoom*HEIGHTD2*(solar_system[i].State.y-HEIGHTD2)/HEIGHTD2)),
                              int(solar_system[i].radius*zoom), 0)
        screen.unlock()
    
        ScanKeyboard()
        updatePositoins(G, solar_system, dt)

        # fragments close enough to touch merge
        for i in range(len(solar_system)):
            if solar_system[i].merged:
                continue
            for j in range(len(solar_system)):
                if solar_system[i] is solar_system[j] or solar_system[j].merged:
                    continue
                if planets_touch(solar_system[i], solar_system[j]):
                    if solar_system[j] is Earth:
                        solar_system[i].merged = True
                        Earth.Mass = Earth.Mass + solar_system[i].Mass
                        break
                    if solar_system[i].Mass < solar_system[j].Mass:
                        if solar_system[i].State.vx < solar_system[j].State.vx:
                            solar_system[i] = solar_system[j]
                            solar_system[j] = solar_system[i]
                            solar_system[j].merged = True
                            newvx = (solar_system[i].State.vx*solar_system[i].Mass+solar_system[j].State.vx*solar_system[j].Mass) / (solar_system[i].Mass+solar_system[j].Mass)
                            newvy = (solar_system[i].State.vy*solar_system[i].Mass+solar_system[j].State.vy*solar_system[j].Mass) / (solar_system[i].Mass+solar_system[j].Mass)
                            solar_system[i].Mass += solar_system[j].Mass 
                            solar_system[i].State.vx = newvx
                            solar_system[i].State.vy = newvy
                            solar_system[i].set_radius_from_mass()

                        if solar_system[i].State.vx > solar_system[j].State.vx:
                            w=1
                            while (solar_system[w].Mass > solar_system[j].Mass):
                                planet_to_split = solar_system[w]
                                split_fraction = 1.0/(randint(split_int_min, split_int_max))
                                massSplit = planet_to_split.Mass * split_fraction 
                                balance_momentum_mass = planet_to_split.Mass - massSplit
                                solar_system[w].Mass = massSplit
                                oldRadius = solar_system[w].radius
                                solar_system[w].set_radius_from_mass()
                                m = (randint(min_adjust_v, max_adjust_v))*10**(-5.0)
                                solar_system[w].State.vx = moon_velocity * m
                                solar_system[w].State.vy = moon_velocity * m
                                Xvelo = ((planet_to_split.Mass * planet_to_split.State.vx) - (solar_system[w].Mass * solar_system[w].State.vx)) / balance_momentum_mass
                                Yvelo = ((planet_to_split.Mass * planet_to_split.State.vy) - (solar_system[w].Mass * solar_system[w].State.vy)) / balance_momentum_mass
                                adjustx = (randint(min_adjust_x, max_adjust_x))/1000.0
                                adjusty = (randint(min_adjust_y, max_adjust_y))/1000.0
                                moon2 = Planet(balance_momentum_mass, solar_system[w].State.x + oldRadius*adjustx, solar_system[w].State.y + oldRadius*adjusty, Xvelo, Yvelo )
                                solar_system.append(moon2)

                                w = w + 1
            #print(t)

        if keysPressed[pygame.K_KP_PLUS]:
            zoom /= 0.99
        if keysPressed[pygame.K_KP_MINUS]:
            zoom /= 1.01
        if keysPressed[pygame.K_ESCAPE]:
            break
        if keysPressed[pygame.K_SPACE]:
            while keysPressed[pygame.K_SPACE]:
                ScanKeyboard()
            bClearScreen = not bClearScreen
            verb = 'show' if bClearScreen else 'hide'
            pygame.display.set_caption('SPACE: %s orbits, keypad +/-: zoom in/out'%verb)
######################################################################################



############################### Running the Program ##################################            
if __name__ == '__main__':
    main() 
######################################################################################

KeyboardInterrupt: 

In [8]:
# Test pygame ***not mine****
import pygame
import math
import solarColorPalette
from planet import planet
 
pygame.init()
 
# Set the width and height of the screen [width, height]
screenWidth = 1024
screenHeight = 768
screenWidthHalf = screenWidth // 2
screenHeightHalf = screenHeight // 2

size = (screenWidth, screenHeight)
screen = pygame.display.set_mode(size)
 
pygame.display.set_caption("Solar System") #set title
#logo = pygame.image.load("solar.gif") #set logo of program
#pygame.display.set_icon(logo)
 
# Loop until the user clicks the close button.
done = False
 
# Used to manage how fast the screen updates
clock = pygame.time.Clock()
#initialize planets
#mercury
mercury = planet('Mercury')
mercury.setColor(solarColorPalette.mercuryColor)
mercury.setWidth(3)
mercury.setRadius(50)
mercury.setSpeed(4.5)
mercury.setX(50)
mercury.setY(250)
#venus
venus = planet('Venus')
venus.setColor(solarColorPalette.venusColor)
venus.setWidth(7)
venus.setRadius(100)
venus.setSpeed(4)
venus.setX(100)
venus.setY(250)
#earth
earth = planet('Earth')
earth.setColor(solarColorPalette.earthColor)
earth.setWidth(6)
earth.setRadius(150)
earth.setSpeed(3)
earth.setX(150)
earth.setY(250)
#mars
mars = planet('Mars')
mars.setColor(solarColorPalette.marsColor)
mars.setWidth(5)
mars.setRadius(180)
mars.setSpeed(2.5)
mars.setX(180)
mars.setY(250)
#jupiter
jupiter = planet('Jupiter')
jupiter.setColor(solarColorPalette.jupiterColor)
jupiter.setWidth(15)
jupiter.setRadius(250)
jupiter.setSpeed(2)
jupiter.setX(250)
jupiter.setY(250)
#saturn
saturn = planet('Saturn')
saturn.setColor(solarColorPalette.saturnColor)
saturn.setWidth(10)
saturn.setRadius(280)
saturn.setSpeed(2.3)
saturn.setX(280)
saturn.setY(250)
saturn.toggleRings()
#uranus
uranus = planet('Uranus')
uranus.setColor(solarColorPalette.uranusColor)
uranus.setWidth(9)
uranus.setRadius(320)
uranus.setSpeed(1.8)
uranus.setX(320)
uranus.setY(250)
#neptune
neptune = planet('Neptune')
neptune.setColor(solarColorPalette.neptuneColor)
neptune.setWidth(8)
neptune.setRadius(350)
neptune.setSpeed(1.2)
neptune.setX(350)
neptune.setY(250)

def drawPlanets(planetIn):
	pygame.draw.circle(screen, solarColorPalette.white, [screenWidthHalf,screenHeightHalf], planetIn.getRadius(), 1)
	pygame.draw.circle(screen, planetIn.getColor(), [planetIn.getX(), planetIn.getY()], planetIn.getWidth(), planetIn.getWidth())
	if planetIn.hasRings() == True:
		pygame.draw.circle(screen, solarColorPalette.white, [planetIn.getX(), planetIn.getY()], planetIn.getWidth()+5, 1)

def movePlanets(planetIn):
	angl = planetIn.getNextAngle()
	planetIn.setX(int(screenWidthHalf + math.sin(angl) * planetIn.getRadius()))
	planetIn.setY(int(screenHeightHalf + math.cos(angl) * planetIn.getRadius()))

# -------- Main Program Loop -----------
while not done:
    # --- Main event loop
    for event in pygame.event.get():
        if event.type == pygame.QUIT:
            done = True
 
    # drawing
    screen.fill(solarColorPalette.black)
    #sun
    pygame.draw.circle(screen, solarColorPalette.yellow, [screenWidthHalf, screenHeightHalf], 40, 40)

    #mercury
    drawPlanets(mercury)
	#venus
    drawPlanets(venus)
    #earth
    drawPlanets(earth)
    #mars
    drawPlanets(mars)
	#jupiter
    drawPlanets(jupiter)
	#saturn
    drawPlanets(saturn)
	#uranus
    drawPlanets(uranus)
	#neptune
    drawPlanets(neptune)

    #Moving the planets along orbit
    movePlanets(mercury)
    movePlanets(venus)
    movePlanets(earth)
    movePlanets(mars)
    movePlanets(jupiter)
    movePlanets(saturn)
    movePlanets(uranus)
    movePlanets(neptune)
    
    pygame.display.flip()
    clock.tick(140)
pygame.quit()

KeyboardInterrupt: 